# A Critical Analysis of Engel and Rogers (1996) Using Data Science

**Michal Fabinger and Quentin Batista**  
_The University of Tokyo_

Using CPI data for U.S. and Canadian cities, Engel and Rogers (1996) (henceforth ER) argued that the variation of price is much higher for two cities located in different countries than for two equidistant cities in the same country. While the paper provides some potential explanation for this border effect, such as nominal price stickiness, the question remained a puzzle. The paper had sizable impact on the Economics literature and was cited over 1,500 times according to Google Scholar. In a follow-up paper, Gorodnichenko and Tesar (2009) (henceforth GT) argued that the border effect identified by ER was in fact driven by the difference in the distribution of prices within the United States and Canada. Below, we complement GT by carefully examining the patterns in the data. Since ER, many data science tools have been developed that allow researchers to extract insights on the patterns in their dataset. In employing  these tools, we find that the model proposed by ER might have been inadequate. The data was obtained directly from Engel's website (https://www.ssc.wisc.edu/~cengel/Data/Border/BorderData.htm).

### Engel and Roger's (1996) Model

ER formulated the hypothesis that the volatility of the prices of similar goods sold in different locations is related to the distance between locations and other explanatory variables including a dummy variable for whether the cities are in different countries. Formally, they use the following regression:

<center>$V\left(P_{j,k}^{i}\right)=\beta_{1}^{i}r_{j,k}+\beta_{2}^{i}B_{j,k}+\sum_{m=1}^{n}\gamma_{m}^{i}D_{m}+u_{j,k}$</center>

- $P_{j,k}^{i}$ is the log of the price of good $i$ in location $j$ relative to the price of good $i$ in location $k$, measured by taking the difference in the log of the relative price between time $t$ and $t-2$.
- $V\left(P_{j,k}^{i}\right)$ is the standard deviation of the relative prices series.
- $r_{j,k}$ is the log distance between location $j$ and $k$.
- $B_{j,k}$ is a dummy variable for whether locations $j$ and $k$ are in different countries.
- $D_{m}$ is a dummy variable for city $m$.
- $u_{j,k}$ is the regression error.

All prices are converted into U.S. dollars using a monthly average exchange rate. ER also consider a filtered measure of $P_{j,k}^{i}$ which uses seasonal dummies. While the original data is actually panel data, taking the standard deviation of the price series reduces it to cross-sectional data. After running this regression, ER found that the coefficient on the log of distance was positive and significant.

### The Data

ER used consumer price data from 23 North American cities for 14 disaggregated consumer price indexes obtained from the Bureau of Labor Statistics. The cities and goods used are described below. The data covered the period between June 1978 and December 1994. 

### Data Preprocessing

We begin our analysis by downloading the dataset and processing for visualization.

In [1]:
import pandas as pd
import numpy as np

# Import Data
US_data_url = 'http://www.ssc.wisc.edu/~cengel/Data/Border/USA.xls'
US_price_data = pd.read_excel(US_data_url, na_values=np.nan).stack(dropna=False).reset_index()
US_L2M_price_data = pd.read_excel(US_data_url, na_values=np.nan).shift(2).stack(dropna=False).reset_index()

CAN_data_url = 'http://www.ssc.wisc.edu/~cengel/Data/Border/CAN.xls'
CAN_price_data = pd.read_excel(CAN_data_url, na_values=np.nan).stack(dropna=False).reset_index()
CAN_L2M_price_data = pd.read_excel(CAN_data_url, na_values=np.nan).shift(2).stack(dropna=False).reset_index()

# Process US Data
# Create common index and merge
US_price_data['JoinIndex'] = US_price_data['level_0'] + \
 US_price_data['level_1']
US_L2M_price_data['JoinIndex'] = US_L2M_price_data['level_0'] + \
 US_L2M_price_data['level_1']
US_price_data = US_price_data.merge(US_L2M_price_data[['JoinIndex', 0]],
                                    how='left', on='JoinIndex')

# Add country column
US_price_data['Country'] = 'US'

# Split date into two columns
US_price_data['Year'], US_price_data['Month'] = \
 zip(*US_price_data['level_0'].map(lambda x: x.split(':')))

# Split city and good code into two columns
US_price_data['CityCode'], US_price_data['GoodCode'] = \
 zip(*US_price_data['level_1'].map(lambda x: (x[:2], x[2:])))

# Process Canadian Data
# Create common index and merge
CAN_price_data['JoinIndex'] = CAN_price_data['level_0'] + \
 CAN_price_data['level_1']
CAN_L2M_price_data['JoinIndex'] = CAN_L2M_price_data['level_0'] + \
 CAN_L2M_price_data['level_1']
CAN_price_data = CAN_price_data.merge(CAN_L2M_price_data[['JoinIndex', 0]],
                                      how='left', on='JoinIndex')

# Add country column
CAN_price_data['Country'] = 'Canada'

# Split date into two columns
CAN_price_data['Year'], CAN_price_data['Month'] = \
 zip(*CAN_price_data['level_0'].map(lambda x: x.split(':')))

# Split city and good code into two columns
CAN_price_data['CityCode'], CAN_price_data['GoodCode'] = \
 zip(*CAN_price_data['level_1'].map(lambda x: (x[:1], x[1:])))

# Merging and cleaning up the dataframe
price_data = pd.concat([US_price_data, CAN_price_data])
price_data = price_data.drop(['level_1', 'JoinIndex'], axis=1)

# Reformat date column
price_data['level_0'] = pd.to_datetime(price_data['level_0'].str.replace(':',
                                                                         '-'))

# Rename columns
price_data.columns = ['Date', 'Price', 'PriceL2M', 'Country', 'Year', 'Month',
                      'CityCode', 'GoodCode']

# Replace negative values by np.nan
price_data.loc[price_data['Price'] < 0, 'Price'] = np.nan
price_data.loc[price_data['PriceL2M'] < 0, 'PriceL2M'] = np.nan

# Reorganize columns
price_data = price_data[['Date', 'Year', 'Month', 'Country', 'CityCode',
                        'GoodCode', 'Price', 'PriceL2M']]

# Reset index
price_data = price_data.reset_index(drop=True)

In [2]:
# Create dictionaries containing good descriptions and city names

goods_desriptions = {"0": "City CPI",
                     "1": "Food at home",
                     "2": "Food away from home",
                     "3": "Alcoholic beverages",
                     "4": "Shelter",
                     "5": "Fuel and other utilities",
                     "6": "Household furnishings & operations",
                     "7": "Men's and boy's apparel",
                     "8": "Women's and girl's apparel",
                     "9": "Footwear",
                     "10": "Private transporation",
                     "11": "Public transporation",
                     "12": "Medical care",
                     "13": "Personal care",
                     "14": "Entertainment"}

city_names = {"CH": "Chicago",
              "LA": "Los Angeles",
              "NY": "New York",
              "PH": "Philadelphia",
              "DA": "Dallas",
              "DT": "Detroit",
              "HS": "Houston",
              "PI": "Pittsburgh",
              "SF": "San Francisco",
              "BA": "Baltimore",
              "BO": "Boston",
              "MI": "Miami",
              "ST": "St. Louis",
              "WA": "Washington, DC",
              "Q": "Quebec",
              "M": "Montreal",
              "O": "Ottawa",
              "T": "Toronto",
              "W": "Winnipeg",
              "R": "Regina",
              "E": "Edmonton",
              "C": "Calgary",
              "V": "Vancouver"}

# Inverse mappings
inv_goods_desriptions = {v: k for k, v in goods_desriptions.items()}
inv_city_names = {v: k for k, v in city_names.items()}

price_data['GoodDescription'] = price_data['GoodCode'].map(goods_desriptions)
price_data['CityName'] = price_data['CityCode'].map(city_names)

### Exploratory Data Analysis

In [3]:
price_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 89947 entries, 0 to 89946
Data columns (total 10 columns):
Date               89947 non-null datetime64[ns]
Year               89947 non-null object
Month              89947 non-null object
Country            89947 non-null object
CityCode           89947 non-null object
GoodCode           89947 non-null object
Price              66541 non-null float64
PriceL2M           66245 non-null float64
GoodDescription    83625 non-null object
CityName           89714 non-null object
dtypes: datetime64[ns](1), float64(2), object(7)
memory usage: 6.9+ MB


In [4]:
price_data.describe()

Price      PriceL2M
count  66541.000000  66245.000000
mean      95.978108     95.752169
std       36.577398     36.445694
min        0.972233      0.972233
25%       78.200000     78.100000
50%      100.300000    100.200000
75%      118.400000    118.100000
max      265.100000    262.700000

In [5]:
price_data.sample(n=15)

Date  Year Month Country CityCode GoodCode   Price  PriceL2M  \
85863 1993-02-01  1993    02  Canada        W        0  129.30    128.50   
60584 1978-08-01  1978    08  Canada        T       14     NaN       NaN   
72444 1985-06-01  1985    06  Canada        V        1   96.20     97.40   
18496 1982-11-01  1982    11      US       PH        1   97.30     99.20   
79445 1989-06-01  1989    06  Canada        M        1  113.70    111.20   
42423 1991-09-01  1991    09      US       SF        3  147.20    143.20   
11905 1980-05-01  1980    05      US       WA       10   84.80     83.80   
17855 1982-08-01  1982    08      US       DT        5   97.20     93.80   
83681 1991-11-01  1991    11  Canada        T        1  114.50    118.30   
30374 1987-03-01  1987    03      US       US     APPI   87.10     86.50   
35134 1989-01-01  1989    01      US       NY        4  144.00    142.80   
49404 1994-04-01  1994    04      US       SF        9  132.30    137.10   
31417 1987-08-01  1987    08      US       BA        7     NaN       NaN   
82203 1990-12-01  1990    12  Canada        T        W   14.98     14.87   
8647  1979-03-01  1979    03      US       HS        7     NaN       NaN   

                GoodDescription        CityName  
85863                  City CPI        Winnipeg  
60584             Entertainment         Toronto  
72444              Food at home       Vancouver  
18496              Food at home    Philadelphia  
79445              Food at home        Montreal  
42423       Alcoholic beverages   San Francisco  
11905     Private transporation  Washington, DC  
17855  Fuel and other utilities         Detroit  
83681              Food at home         Toronto  
30374                       NaN             NaN  
35134                   Shelter        New York  
49404                  Footwear   San Francisco  
31417   Men's and boy's apparel       Baltimore  
82203                       NaN         Toronto  
8647    Men's and boy's apparel         Houston

In [6]:
# Start date
price_data.Date.head(1)

0   1976-01-01
Name: Date, dtype: datetime64[ns]

In [7]:
# End date
price_data.Date.tail(1)

89946   1995-05-01
Name: Date, dtype: datetime64[ns]

In [8]:
from bokeh.plotting import figure, show, output_notebook, gridplot
from bokeh.models import ColumnDataSource, HoverTool
from bokeh.palettes import all_palettes

output_notebook()

TOOLS = "crosshair,pan,wheel_zoom,reset,tap,save"

colors = all_palettes['Category20'][len(goods_desriptions)]

grid = []
plot_list = []

for city_code in city_names:
    hover = HoverTool(tooltips=[
        ("index", "$index"),
        ("good type", "@good"),
        ("(x,y)", "($x, $y)"),
    ])

    p = figure(x_axis_type="datetime", tools=[TOOLS, hover], plot_width=400,
               plot_height=400)
    p.title.text = city_names[city_code]
    p.title.align = 'center'

    for good_code in goods_desriptions:
        condition = (price_data['CityCode'] == city_code) & \
         (price_data['GoodCode'] == good_code)
        source = ColumnDataSource(data=dict(
            x=price_data['Date'][condition],
            y=price_data['Price'][condition],
            good=price_data['GoodDescription'][condition]))

        p.line(x='x', y='y', color=colors[int(good_code)], source=source)

    if len(plot_list) < 2:
        plot_list.append(p)
    else:
        grid.append(plot_list)
        plot_list = []
        plot_list.append(p)

if plot_list:
    grid.append(plot_list)

p = gridplot(grid)

show(p)

Loading BokehJS ...

There is a significant amount of missing data points in the data (about 25%). Additionally, many U.S. cities actually have data only for one type of good: food at home. 

# Visualization

Before further manipulating the data, we normalize the series based on the 1980-1981 price index.

In [9]:
def mean_init_price_index(price_type, city_code, good_code):
    index = price_data[(price_data['CityCode'] == city_code) &
                       (price_data['GoodCode'] == good_code) &
                       price_data['Year'].isin(['1980', '1981'])][
                           price_type].mean()
    return index


def data_normalization(df, col_to_normalize, city_names, goods_desriptions):
    for city_code in city_names:
        for good_code in goods_desriptions:
            condition = (df['CityCode'] == city_code) & \
             (df['GoodCode'] == good_code)
            df.loc[condition, col_to_normalize + 'N'] = \
                df[col_to_normalize][condition] / \
                mean_init_price_index(col_to_normalize, city_code, good_code)

data_normalization(price_data, 'Price', city_names, goods_desriptions)
data_normalization(price_data, 'PriceL2M', city_names, goods_desriptions)

In [13]:
from ipywidgets import interact
import flexx
from bokeh.models import Legend

TOOLS = "crosshair,hover,pan,wheel_zoom,reset,tap,save"

p_cities = figure(x_axis_type="datetime", tools=TOOLS, plot_width=800,
                  plot_height=600, toolbar_location="above",
                  title='Evolution of Prices by Cities')

colors = all_palettes['Category20'][len(goods_desriptions)]

lines = []
legend_it = []

for good_code in goods_desriptions:
    condition = (price_data['CityCode'] == 'CH') & \
     (price_data['GoodCode'] == good_code)
    temp_line = p_cities.line(x=price_data['Date'][condition],
                              y=price_data['PriceN'][condition],
                              color=colors[int(good_code)])
    lines.append(temp_line)
    legend_it.append((goods_desriptions[good_code], [temp_line]))

    
def city_plot_update(City):
    for line, good_code in zip(lines, goods_desriptions):
        condition = (price_data['CityCode'] == inv_city_names[City]) & \
         (price_data['GoodCode'] == good_code)
        line.data_source.data['x'] = price_data['Date'][condition]
        line.data_source.data['y'] = price_data['PriceN'][condition]
    show(p_cities)

legend = Legend(items=legend_it, location=(0, 100))
legend.click_policy = "hide"

p_cities.add_layout(legend, 'right')

p_cities.title.text_font_size = '12pt'
p_cities.yaxis.axis_label = 'Normalized Price Index'
p_cities.xaxis.axis_label = 'Year'

interact(city_plot_update, City=city_names.values())

<function __main__.city_plot_update>

In [17]:
from bokeh.palettes import magma

p_goods = figure(x_axis_type="datetime", tools=TOOLS, plot_width=800,
                 plot_height=600, toolbar_location="above",
                  title='Evolution of Prices by Cities')

lines = []
legend_it = []
colors = magma(len(city_names))

for (i, city) in enumerate(city_names):
    condition = (price_data['CityCode'] == city) & \
     (price_data['GoodCode'] == '0')
    temp_line = p_goods.line(x=price_data['Date'][condition],
                            y=price_data['PriceN'][condition],
                            color=colors[i])
    lines.append(temp_line)
    legend_it.append((city_names[city], [temp_line]))


def good_plot_update(Good):
    for line, city in zip(lines, city_names):
        condition = (price_data['CityCode'] == city) & \
         (price_data['GoodCode'] == inv_goods_desriptions[Good])
        line.data_source.data['x'] = price_data['Date'][condition]
        line.data_source.data['y'] = price_data['PriceN'][condition]
    show(p_goods)

legend = Legend(items=legend_it, location=(0, 25))
legend.click_policy = "hide"

p_goods.add_layout(legend, 'right')

interact(good_plot_update, Good=goods_desriptions.values())

<function __main__.good_plot_update>

In [15]:
p_countries = figure(x_axis_type="datetime", tools=TOOLS, plot_width=600,
                     plot_height=600, toolbar_location="above",
                     title='Evolution of Prices by Countries')

lines = []

for (i, city) in enumerate(city_names):
    condition = (price_data['CityCode'] == city) & \
     (price_data['GoodCode'] == '0')
    if len(city) == 2:
        temp_line = p_countries.line(x=price_data['Date'][condition],
                                     y=price_data['PriceN'][condition],
                                     color='blue',
                                     legend='US Cities')
    else:
        temp_line = p_countries.line(x=price_data['Date'][condition],
                                     y=price_data['PriceN'][condition],
                                     color='red', 
                                     legend='Canadian Cities')
    lines.append(temp_line)
    
def countries_plot_update(Good):
    for line, city in zip(lines, city_names):
        condition = (price_data['CityCode'] == city) & \
         (price_data['GoodCode'] == inv_goods_desriptions[Good])
        line.data_source.data['x'] = price_data['Date'][condition]
        line.data_source.data['y'] = price_data['PriceN'][condition]
    show(p_countries)

p_countries.legend.location = 'bottom_right'
p_countries.title.text_font_size = '12pt'
p_countries.yaxis.axis_label = 'Normalized Price Index'
p_countries.xaxis.axis_label = 'Year'

interact(countries_plot_update, Good=goods_desriptions.values())

<function __main__.countries_plot_update>

# Discussion

Below, we discuss the various factors that suggest that the model employed by ER may have been inadequate. More precisely, we suspect that the model suffers from omitted-variable bias and endogeneity of some of the regressors.

### Shelter

Between 1985 and 1989, the average price of a house in the Greater Toronto Area increased by 113%. At first fueled by low unemployment and a large inflow of immigrants, the price increase subsequently attracted massive speculative investment, thereby creating a housing bubble. While the bubble was mostly concentrated in the Toronto area, it also impacted other Canadian cities. In fact, we can observe a sharp increase in shelter prices for Canadian cities for ER. Additionally, the 1980 oil glut led to a deep recession in Canadian regions whose economy is deeply reliant on the production and sale of oil, which explains the sharp decline observed in the data on Calgary. Both of these factors contributed to increasing the disparity in prices between U.S. and Canadian cities. Finally, since housing is not subject to international arbitrage, it is natural that the behavior of prices would differ in both countries.

### Private Transportation

In 1981, with the American auto industry mired in recession, Japanese car makers agreed to limit exports of passenger cars to the United States. This "voluntary export restraint" (VER) program allowed only 1.68 million Japanese cars into the U.S. each year. The cap was raised to 1.85 million cars in 1984, and to 2.30 million in 1985 (representing about 20% of the car market at that time), before the program was terminated in 1994. Besides, the effect of this program interacted with the impact of significant movements in exchange rates. Between 1985 and 1990, the yen significantly appreciated against the dollar by close to 50%. Meanwhile, the Canadian dollar significantly depreciated against the dollar between 1980 and 1986, then appreciated until 1991, before depreciating again until 1995. These changes potentially created supply shocks in the car markets of both countries, leading to price disparities which the model did not seem to explain.

### Public transportation

While changes in the prices of buses and trains are events to consider, public transportation is generally a highly regulated industry where prices are set by the government. As such, events such as a budget crisis can push the government to increase prices. Besides, the cost of public transportation is also related to the coverage distance and weather conditions because they both impact the cost of building and maintaining a public transportation network. None of those factors are however directly included in the regression model.

### Alcoholic beverages

Alcoholic beverages are generally subject to significant taxes, which makes their prices easily susceptible to country-specific fluctuations. In fact, the impact of the 1991 U.S. Federal Alcohol Tax increase can be observed in the data. As such, they are not well-suited for this model.

### Fuel and other utilities

Many utilities are highly regulated, suggesting a similar issue to the public transportation case. Additionally, inspecting the fluctuations in Chicago reveals some unexplained patterns, potentially indicating some data quality issues.

### Food away from home

This type of good has a highly non-tradable component. For example, the dining experience of a restaurant in New York cannot be enjoyed in Toronto. Thus, this type of good is not well-suited for this model.

### Personal care

Similarly to food away from home, this type of good also has a highly non-tradable component. In most cases, personal care services are location specific, and therefore not subject to international arbitrage.

### Medical Care

Medical care tends to be a regulated, non-tradable industry. Prices largely depends on government policies, and are therefore susceptible to country-specific shocks. Additionally, prices are set on an annual basis in Canada which explains why we observe jumps, while in the U.S., prices are set on a monthly basis which is why we observe smooth price increases in the data. As such, factors such as how the data is aggregated among providers partially drives the discrepancies in prices. 

### Apparel & Footwear

U.S. prices are highly volatile starting from the late 1980s, suggesting that they may not have been properly recorded. City-specific measurement error would imply that the dummy variable for cities is correlated with the error term, and therefore that the model suffers from endogeneity. Additionally, according to the data, the price of women and girl's apparel was on average close to 40% higher in New York compared to Philadelphia in the mid-1990s. Given that the two cities are less than a two-hour drive away from each other, the significant price difference appears highly implausible. Once again, this observation points to data quality issues. A potential explanation would be that the average quality of goods is actually different across cities, in which case, this should be accounted for in the regression.

### Tax Increase in Canada

In January 1991, the Canadian government implemented a 7% VAT tax. This tax had a significant impact on the prices of goods and services and can be observed in many time series such as that of apparel, footwear, and food away from home. Since this tax is not subject to arbitrage, it naturally contributed to the price dispersion between the U.S. and Canada.

# References

Engel, Charles, and John H. Rogers. 1996. “How Wide Is the Border?” American Economic Review 86(5):1112–25.

Gorodnichenko, Yuriy, and Linda L. Tesar. 2009. "Border Effect or Country Effect? Seattle May Not Be So Far from Vancouver After All." American Economic Journal: Macroeconomics, 1(1): 219-41.

Benjamin, Daniel K. (September 1999). "Voluntary Export Restraints on Automobiles"